In [1]:
from datasets import load_dataset

dataset = load_dataset("Gholamreza/pquad")


/home/firouzi/embedding_model/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
all_dataset = []
for data in dataset["train"]:
    if len(data["answers"]["text"]) > 0:
        all_dataset.append({'question': data['question'], 'passage_positive': [data['context']], 'passage_negative': [], 'passage_negative_random': []})
    # else:
    #     all_dataset.append({'question': data['question'], 'passage_positive': [], 'passage_negative': [data['context']]})

print(len(all_dataset))
print(len(dataset["train"]))

48273
63994


In [4]:
print(all_dataset[1241])

{'question': 'سام میرزا در چه تاریخی توسط نادرشاه دستگیر شد؟', 'passage_positive': ['این ضربت سخت خیال نادر را پریشان کرد و رضا قلی میرزا را که در رکاب بود در طهران گذاشت و خود به داغستان رفت در این سفر اگرچه بعضی از رؤسای طوایف لزکی از در اطاعت درآمدند لیکن غالب سکنه داغستان به قلل جبال پرارتفاع پناه گرفتند و از هر طرف به تعرّض اردوی نادر دست زدند و لطمات بسیار به ایشان وارد آوردند حتّی موقعی به خیمه خود نادر نیز تعرّض رساندند. در رمضان ۱۱۵۴ موقعیکه نادر هنوز در داغستان بود غلامی را که مرتکب انداختن تیر در جنگل سوادکوه شده بود بخدمت او آوردند. نادر او را کور کرد. شخصی بنام سام میرزا که به ادّعای فرزندی شاه سلطان حسین در آذربایجان به سلطنت طلبی برخاسته و محمّد خان پسر سرخای خان لزگی و خوانین دربند و داغستان را با خود همدست نموده بود. نادر توسّط نصر اللّه میرزا و چند تن از سرداران خود انقلاب این حدود را بالاخره خواباند و سام میرزا در ذی\u200cالقعده ۱۱۵۶ دستگیر گردید.'], 'passage_negative': [], 'passage_negative_random': []}


In [3]:
dataset["train"][1251]

{'id': 123802.0,
 'title': 'قرن نوزدهم',
 'context': 'جنگ داخلی ایالات متحده از سال ۱۸۶۱ تا ۱۸۶۵ طول کشید. در طول جنگ آبراهام لینکلن رئیس\u200cجمهور بود. امروزه او را به عنوان یکی از بزرگ\u200cترین رهبران جهان غرب تلقی می\u200cکنند. در همین زمان، آمدن نیروی بخار در کنار انقلاب صنعتی رو به رشد، گسترش شدیدی در کارخانجات صنعتی ایجاد کرد. در سال ۱۸۷۸ توماس ادیسون لامپ برق جدید خود را به نمایش گذاشت و در طول یک دهه سیستم توزیع برق بزرگی را در تمام کشور راه\u200cاندازی کرد. تأثیر اقتصادی به تدریج به خارج از ایالات متحده و به سمت اقیانوس آرام و آمریکای لاتین گسترش پیدا کرد.',
 'question': 'علت گسترش شدید کارخانجات صنعتی چه بود؟',
 'answers': {'text': ['آمدن نیروی بخار در کنار انقلاب صنعتی رو به رشد'],
  'answer_start': [180]}}

In [33]:
from hazm import Normalizer
import requests
import numpy as np
from dotenv import load_dotenv
import os

load_dotenv()


class TextEmbedder:
    def __init__(self, model_name="BAAI/bge-m3"):
        self.model_name = model_name
        self.headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('EMBEDDING_PASS')}"}
        self.normalizer = Normalizer()
    
    def preprocess_embedder(self, text:str):
        text = text.replace("\n", ".")
        text = self.normalizer.normalize(text)
        
        return text
    

    def embed_texts(self, texts:list[str])->list[list[float]]:
        """
        Embed texts using the model.
        """
        if texts == []:
            return []
            
        texts = [self.preprocess_embedder(text) for text in texts]
        
        payload = {
            "model": self.model_name,
            "input": texts
        }
        responses = requests.post("http://78.38.161.78:3094/v1/embeddings", headers=self.headers, json=payload)
        embeddings = [np.array(response["embedding"]) for response in responses.json()["data"]]
        
        return embeddings
      

In [ ]:
import random
from tqdm import tqdm
import numpy as np

THRESHOLD_MULTIPLY = 0.9
RANDOM_NEGATIVE_COUNT = 50
batch_size = 50

all_dataset = all_dataset[1500:1500+220]

text_embedder = TextEmbedder()
len_dataset = len(all_dataset)
all_dataset_embeddings = [{'question_embedding': "", 'passage_positive_embedding': [], 'passage_negative_embeddings': []} for _ in range(len_dataset)]

print("calculate question embeddings")
# calculate question embeddings
for i in tqdm(range(0, len_dataset, batch_size)):

    question_list = []
    for id in range(i, min(i + batch_size, len_dataset)):
        question_list.append(all_dataset[id]['question'])

    question_embeddings = text_embedder.embed_texts(question_list)

    count = 0   
    for id in range(i, min(i + batch_size, len_dataset)):
        all_dataset_embeddings[id]['question_embedding'] = question_embeddings[count]
        count += 1


print("calculate passage positive embeddings")
# calculate passage positive embeddings
for i in tqdm(range(0, len_dataset, batch_size)):

    passage_positive_list = []
    for id in range(i, min(i + batch_size, len_dataset)):
        for passage in all_dataset[id]['passage_positive']:
            passage_positive_list.append(passage)

    passage_positive_embeddings = text_embedder.embed_texts(passage_positive_list)

    count = 0
    for id in range(i, min(i + batch_size, len_dataset)):
        for passage_id in range(len(all_dataset[id]['passage_positive'])):
            all_dataset_embeddings[id]['passage_positive_embedding'].append(passage_positive_embeddings[count])
            count += 1

print("calculate passage negative embeddings")
# calculate passage negative embeddings
for i in tqdm(range(0, len_dataset, batch_size)):

    passage_negative_list = []
    for id in range(i, min(i + batch_size, len_dataset)):
        for passage in all_dataset[id]['passage_negative']:
            passage_negative_list.append(passage)

    passage_negative_embeddings = text_embedder.embed_texts(passage_negative_list)

    count = 0
    for id in range(i, min(i + batch_size, len_dataset)):
        for passage_id in range(len(all_dataset[id]['passage_negative'])):
            all_dataset_embeddings[id]['passage_negative_embeddings'].append(passage_negative_embeddings[count])
            count += 1

print("getting random negative passages")
for id in tqdm(range(len_dataset)):
    question_embeddings = all_dataset_embeddings[id]['question_embedding']
    passage_positive_embeddings = all_dataset_embeddings[id]['passage_positive_embedding'][0]

    score_question_passage_positive = np.dot(question_embeddings, passage_positive_embeddings)

    while len(all_dataset[id]['passage_negative_random']) < RANDOM_NEGATIVE_COUNT:
        random_id = random.randint(0, len_dataset - 1)
        if random_id != id:
            all_passages_embedding = all_dataset_embeddings[random_id]['passage_negative_embeddings'] + all_dataset_embeddings[random_id]['passage_positive_embedding']
            all_passages = all_dataset[random_id]['passage_negative'] + all_dataset[random_id]['passage_positive']
            random_passage_id = random.randint(0, len(all_passages) - 1)
            random_passage_embeddings = all_passages_embedding[random_passage_id]
            score_question_random_passage = np.dot(question_embeddings, random_passage_embeddings)

            if score_question_random_passage < THRESHOLD_MULTIPLY * score_question_passage_positive:
                all_dataset[id]['passage_negative_random'].append(all_passages[random_passage_id])


calculate question embeddings


100%|██████████| 5/5 [00:00<00:00,  6.35it/s]


calculate passage positive embeddings


100%|██████████| 5/5 [00:01<00:00,  4.47it/s]


calculate passage negative embeddings


100%|██████████| 5/5 [00:00<00:00, 21140.65it/s]


getting random negative passages


100%|██████████| 220/220 [00:00<00:00, 3699.93it/s]


In [4]:
len(all_dataset[:100])

100

In [5]:
import json

with open("./x.json", 'w', encoding='utf-8') as f:
    json.dump(all_dataset[:100], f, ensure_ascii=False, indent=4)